In [2]:
import gensim
import pandas as pd
import numpy as np
from gensim.models import LdaModel, LsiModel
from sklearn.feature_extraction.text import TfidfVectorizer
import nltk

In [3]:
df = pd.read_csv ('Sample.csv')
df

Full Text
0     @hamcore_ First the boss metal zone schematics...
1     @sippygup its in the vaccine and 5g makes it m...
2     Him and all the others that do Not like and ha...
3     @TimRunsHisMouth Him and all the others that d...
4     @NYGovCuomo 99.97% survival rate no vaccine fo...
...                                                 ...
9953  Waiting for the train and I hear two mfs say �...
9954  I played my radical left avant garde music and...
9955  You are such a fag @MayorKeller And what the F...
9956  .@seanspicer hahahaha Trump's accomplishments?...
9957  100%. It was about the election, not the virus...

[9958 rows x 1 columns]

In [4]:
%pylab inline

import pandas as pd
import pickle as pk
from scipy import sparse as sp

Populating the interactive namespace from numpy and matplotlib


In [6]:
p_df = pd.read_csv('Sample.csv')
docs = array(p_df['Full Text'])

In [7]:
from nltk.stem.wordnet import WordNetLemmatizer
from nltk.tokenize import RegexpTokenizer

def docs_preprocessor(docs):
    tokenizer = RegexpTokenizer(r'\w+')
    for idx in range(len(docs)):
        docs[idx] = docs[idx].lower()  # Convert to lowercase.
        docs[idx] = tokenizer.tokenize(docs[idx])  # Split into words.

    # Remove numbers, but not words that contain numbers.
    docs = [[token for token in doc if not token.isdigit()] for doc in docs]
    
    # Remove words that are only one character.
    docs = [[token for token in doc if len(token) > 3] for doc in docs]
    
    # Lemmatize all words in documents.
    lemmatizer = WordNetLemmatizer()
    docs = [[lemmatizer.lemmatize(token) for token in doc] for doc in docs]
  
    return docs

In [8]:
docs = docs_preprocessor(docs)

In [9]:
docs

[['hamcore_',
  'first',
  'bos',
  'metal',
  'zone',
  'schematic',
  'vaccine',
  'hitler',
  'stuff',
  'right',
  'cmon',
  'only',
  '42am'],
 ['sippygup', 'vaccine', 'make', 'more', 'powerful', 'watch'],
 ['others',
  'that',
  'like',
  'hate',
  'donaldtrump',
  'just',
  'because',
  'they',
  'part',
  'satanic',
  'deep',
  'state',
  'illuminati',
  'serf',
  'different',
  'same',
  'that',
  'gave',
  'power',
  'poisoning',
  'food',
  'water',
  'that',
  'monsanto',
  'plus',
  'behind',
  'vaccine',
  'withvp'],
 ['timrunshismouth',
  'others',
  'that',
  'like',
  'hate',
  'donaldtrump',
  'just',
  'because',
  'they',
  'part',
  'satanic',
  'deep',
  'state',
  'illuminati',
  'serf',
  'different',
  'same',
  'that',
  'gave',
  'power',
  'poisoning',
  'food',
  'water',
  'that',
  'monsanto',
  'plus',
  'behind',
  'vaccine',
  'withvp'],
 ['nygovcuomo', 'survival', 'rate', 'vaccine'],
 ['and_kell',
  'only',
  'coincidence',
  'extremely',
  'rare',
  

In [10]:
from gensim.models import Phrases
# Add bigrams and trigrams to docs (only ones that appear 10 times or more).
bigram = Phrases(docs, min_count=10)
trigram = Phrases(bigram[docs])

for idx in range(len(docs)):
    for token in bigram[docs[idx]]:
        if '_' in token:
            # Token is a bigram, add to document.
            docs[idx].append(token)
    for token in trigram[docs[idx]]:
        if '_' in token:
            # Token is a bigram, add to document.
            docs[idx].append(token)

In [11]:
from gensim.corpora import Dictionary

# Create a dictionary representation of the documents.
dictionary = Dictionary(docs)
print('Number of unique words in initital documents:', len(dictionary))

# Filter out words that occur less than 10 documents, or more than 20% of the documents.
dictionary.filter_extremes(no_below=10, no_above=0.2)
print('Number of unique words after removing rare and common words:', len(dictionary))

Number of unique words in initital documents: 20173
Number of unique words after removing rare and common words: 2354


In [12]:
corpus = [dictionary.doc2bow(doc) for doc in docs]


In [13]:
print('Number of unique tokens: %d' % len(dictionary))
print('Number of documents: %d' % len(corpus))

Number of unique tokens: 2354
Number of documents: 9958


In [14]:
from gensim.models import LdaModel


In [21]:
# Set training parameters.
num_topics = 50
chunksize = 500 # size of the doc looked at every pass
passes = 0 # number of passes through documents
iterations = 400
eval_every = 1  # Don't evaluate model perplexity, takes too much time.

# Make a index to word dictionary.
temp = dictionary[0]  # This is only to "load" the dictionary.
id2word = dictionary.id2token

%time model = LdaModel(corpus=corpus, id2word=id2word, chunksize=chunksize, \
                       alpha='auto', eta='auto', \
                       iterations=iterations, num_topics=num_topics, \
                       passes=passes, eval_every=eval_every)

Wall time: 35.9 ms


In [23]:
import pyLDAvis
pyLDAvis.enable_notebook()
import pyLDAvis.gensim_models
import warnings
warnings.filterwarnings("ignore", category=DeprecationWarning) 

In [24]:
pyLDAvis.gensim_models.prepare(model, corpus, dictionary)


PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
14    -0.000177 -0.000116       1        1  5.344005
20    -0.000253 -0.000235       2        1  4.879015
35     0.000058 -0.000454       3        1  3.384831
10    -0.000035 -0.000266       4        1  2.970444
33    -0.000024  0.000260       5        1  2.873987
49     0.000036  0.000099       6        1  2.852253
0     -0.000907  0.000531       7        1  2.827366
3     -0.000328 -0.000172       8        1  2.819656
11     0.000352  0.000210       9        1  2.699342
43    -0.000326 -0.000156      10        1  2.525538
47     0.000486  0.000083      11        1  2.507195
31     0.000328 -0.000068      12        1  2.413676
32     0.000136 -0.000013      13        1  2.408472
30    -0.000111 -0.000014      14        1  2.354086
6     -0.000069  0.000297      15        1  2.348929
17    -0.000161  0.000089      16        1  2.236513
15     0.000219 -0.000469      17        1  2.236193
5      0.000020  0.000103      18        1  2.173109
42     0.000111 -0.000234      19        1  2.149864
4     -0.000263  0.000183      20        1  2.114054
23    -0.000088 -0.000040      21        1  1.997927
44    -0.000282 -0.000062      22        1  1.973576
34    -0.000430  0.000229      23        1  1.936978
1     -0.000200 -0.000473      24        1  1.927155
16     0.000189 -0.000342      25        1  1.895329
25    -0.000193 -0.000238      26        1  1.853924
7      0.000350 -0.000039      27        1  1.808878
21    -0.000412 -0.000132      28        1  1.791678
19    -0.000245  0.000840      29        1  1.754328
8      0.000285  0.000089      30        1  1.697268
39     0.000109  0.000195      31        1  1.683767
9     -0.000253  0.000029      32        1  1.630698
12    -0.000316 -0.000231      33        1  1.619884
37     0.000394  0.000771      34        1  1.542892
29    -0.000425  0.000089      35        1  1.525919
38     0.000390  0.000201      36        1  1.472899
24    -0.000310 -0.000124      37        1  1.403070
28    -0.000382 -0.000626      38        1  1.384405
45    -0.000181  0.000369      39        1  1.303527
26     0.000065 -0.000354      40        1  1.288026
27     0.000130 -0.000095      41        1  1.260516
13     0.000061 -0.000100      42        1  1.259812
46     0.000362  0.000406      43        1  1.136041
18     0.000248  0.000285      44        1  1.080384
41     0.000343 -0.000315      45        1  1.064185
22     0.000526 -0.000446      46        1  1.015704
40     0.000126  0.000193      47        1  0.978460
48     0.000219  0.000061      48        1  0.918726
2      0.000317  0.000229      49        1  0.894632
36     0.000514 -0.000026      50        1  0.780881, topic_info=                Term       Freq      Total Category  logprob  loglift
2124          reward  71.000000  71.000000  Default  30.0000  30.0000
1033  washingtonpost  70.000000  70.000000  Default  29.0000  29.0000
1676        dbongino  69.000000  69.000000  Default  28.0000  28.0000
1744        altering  70.000000  70.000000  Default  27.0000  27.0000
1145          father  70.000000  70.000000  Default  26.0000  26.0000
...              ...        ...        ...      ...      ...      ...
1702          damage   0.681671  72.013717  Topic50  -7.5512   0.1924
2164  richardgrenell   0.673842  71.025328  Topic50  -7.5628   0.1947
1828       reporting   0.675694  71.516246  Topic50  -7.5600   0.1906
194     citizen_with   0.671738  71.216769  Topic50  -7.5659   0.1889
885        when_come   0.673100  71.849653  Topic50  -7.5639   0.1821

[1824 rows x 6 columns], token_table=      Topic      Freq        Term
term                             
2058      1  0.057156  99freemind
2058      2  0.042867  99freemind
2058      3  0.028578  99freemind
2058      4  0.028578  99freemind
2058      5  0.028578  99freemind
...     ...       ...         ...
7        46  0.013827        zone
7        47  0.01

In [25]:
# use the lda model to transform documents
lda_docs = model[corpus]
for row in lda_docs:
    print (row)

[(37, 0.9108686)]
[(7, 0.8039064)]
[(14, 0.9591477)]
[(14, 0.9591477)]
[(41, 0.8599378)]
[(43, 0.9573714)]
[(5, 0.89105856)]
[(10, 0.83659405)]
[(2, 0.8599347)]
[(19, 0.95737094)]
[(20, 0.96368694)]
[(26, 0.92996705)]
[(8, 0.93463635)]
[(23, 0.9423264)]
[(42, 0.96368647)]
[(20, 0.96368676)]
[(12, 0.9573715)]
[(0, 0.02), (1, 0.02), (2, 0.02), (3, 0.02), (4, 0.02), (5, 0.02), (6, 0.02), (7, 0.02), (8, 0.02), (9, 0.02), (10, 0.02), (11, 0.02), (12, 0.02), (13, 0.02), (14, 0.02), (15, 0.02), (16, 0.02), (17, 0.02), (18, 0.02), (19, 0.02), (20, 0.02), (21, 0.02), (22, 0.02), (23, 0.02), (24, 0.02), (25, 0.02), (26, 0.02), (27, 0.02), (28, 0.02), (29, 0.02), (30, 0.02), (31, 0.02), (32, 0.02), (33, 0.02), (34, 0.02), (35, 0.02), (36, 0.02), (37, 0.02), (38, 0.02), (39, 0.02), (40, 0.02), (41, 0.02), (42, 0.02), (43, 0.02), (44, 0.02), (45, 0.02), (46, 0.02), (47, 0.02), (48, 0.02), (49, 0.02)]
[(9, 0.9019547)]
[(0, 0.02), (1, 0.02), (2, 0.02), (3, 0.02), (4, 0.02), (5, 0.02), (6, 0.02), (7, 

[(29, 0.95331186)]
[(35, 0.9622896)]
[(47, 0.9245771)]
[(24, 0.9607801)]
[(30, 0.97116256)]
[(47, 0.8910653)]
[(42, 0.924579)]
[(9, 0.92996705)]
[(25, 0.910866)]
[(12, 0.7548688)]
[(20, 0.95097554)]
[(31, 0.9299667)]
[(49, 0.95543367)]
[(0, 0.02), (1, 0.02), (2, 0.02), (3, 0.02), (4, 0.02), (5, 0.02), (6, 0.02), (7, 0.02), (8, 0.02), (9, 0.02), (10, 0.02), (11, 0.02), (12, 0.02), (13, 0.02), (14, 0.02), (15, 0.02), (16, 0.02), (17, 0.02), (18, 0.02), (19, 0.02), (20, 0.02), (21, 0.02), (22, 0.02), (23, 0.02), (24, 0.02), (25, 0.02), (26, 0.02), (27, 0.02), (28, 0.02), (29, 0.02), (30, 0.02), (31, 0.02), (32, 0.02), (33, 0.02), (34, 0.02), (35, 0.02), (36, 0.02), (37, 0.02), (38, 0.02), (39, 0.02), (40, 0.02), (41, 0.02), (42, 0.02), (43, 0.02), (44, 0.02), (45, 0.02), (46, 0.02), (47, 0.02), (48, 0.02), (49, 0.02)]
[(36, 0.8910625)]
[(1, 0.32653505), (25, 0.57741755)]
[(22, 0.92996573)]
[(47, 0.95543325)]
[(30, 0.87743723)]
[(25, 0.9182934)]
[(35, 0.95331)]
[(4, 0.85993874)]
[(44, 0.83

[(23, 0.92457956)]
[(29, 0.96498317)]
[(21, 0.9591483)]
[(20, 0.8365927)]
[(16, 0.955433)]
[(43, 0.93463504)]
[(20, 0.94839835)]
[(41, 0.9509765)]
[(0, 0.02), (1, 0.02), (2, 0.02), (3, 0.02), (4, 0.02), (5, 0.02), (6, 0.02), (7, 0.02), (8, 0.02), (9, 0.02), (10, 0.02), (11, 0.02), (12, 0.02), (13, 0.02), (14, 0.02), (15, 0.02), (16, 0.02), (17, 0.02), (18, 0.02), (19, 0.02), (20, 0.02), (21, 0.02), (22, 0.02), (23, 0.02), (24, 0.02), (25, 0.02), (26, 0.02), (27, 0.02), (28, 0.02), (29, 0.02), (30, 0.02), (31, 0.02), (32, 0.02), (33, 0.02), (34, 0.02), (35, 0.02), (36, 0.02), (37, 0.02), (38, 0.02), (39, 0.02), (40, 0.02), (41, 0.02), (42, 0.02), (43, 0.02), (44, 0.02), (45, 0.02), (46, 0.02), (47, 0.02), (48, 0.02), (49, 0.02)]
[(45, 0.96498287)]
[(44, 0.89106065)]
[(44, 0.96837187)]
[(40, 0.9573706)]
[(5, 0.8039062)]
[(18, 0.4996473), (20, 0.4317465)]
[(12, 0.95331144)]
[(31, 0.9483975)]
[(31, 0.94553095)]
[(34, 0.8599371)]
[(30, 0.9693603)]
[(35, 0.9673184)]
[(17, 0.9346359)]
[(8, 0.

[(7, 0.89105797)]
[(34, 0.9533106)]
[(42, 0.8365906)]
[(0, 0.02), (1, 0.02), (2, 0.02), (3, 0.02), (4, 0.02), (5, 0.02), (6, 0.02), (7, 0.02), (8, 0.02), (9, 0.02), (10, 0.02), (11, 0.02), (12, 0.02), (13, 0.02), (14, 0.02), (15, 0.02), (16, 0.02), (17, 0.02), (18, 0.02), (19, 0.02), (20, 0.02), (21, 0.02), (22, 0.02), (23, 0.02), (24, 0.02), (25, 0.02), (26, 0.02), (27, 0.02), (28, 0.02), (29, 0.02), (30, 0.02), (31, 0.02), (32, 0.02), (33, 0.02), (34, 0.02), (35, 0.02), (36, 0.02), (37, 0.02), (38, 0.02), (39, 0.02), (40, 0.02), (41, 0.02), (42, 0.02), (43, 0.02), (44, 0.02), (45, 0.02), (46, 0.02), (47, 0.02), (48, 0.02), (49, 0.02)]
[(10, 0.9455297)]
[(40, 0.9423238)]
[(42, 0.95331025)]
[(44, 0.97028893)]
[(7, 0.95737034)]
[(46, 0.9387216)]
[(25, 0.94553053)]
[(44, 0.96935993)]
[(49, 0.96229017)]
[(25, 0.9573695)]
[(29, 0.9108674)]
[(11, 0.9661903)]
[(35, 0.9245787)]
[(10, 0.9573711)]
[(14, 0.94839644)]
[(44, 0.9533107)]
[(15, 0.9573712)]
[(27, 0.8039116)]
[(4, 0.94553024)]
[(31, 0

[(16, 0.8910562)]
[(0, 0.9711626)]
[(34, 0.92996603)]
[(12, 0.9622894)]
[(9, 0.95331216)]
[(0, 0.02), (1, 0.02), (2, 0.02), (3, 0.02), (4, 0.02), (5, 0.02), (6, 0.02), (7, 0.02), (8, 0.02), (9, 0.02), (10, 0.02), (11, 0.02), (12, 0.02), (13, 0.02), (14, 0.02), (15, 0.02), (16, 0.02), (17, 0.02), (18, 0.02), (19, 0.02), (20, 0.02), (21, 0.02), (22, 0.02), (23, 0.02), (24, 0.02), (25, 0.02), (26, 0.02), (27, 0.02), (28, 0.02), (29, 0.02), (30, 0.02), (31, 0.02), (32, 0.02), (33, 0.02), (34, 0.02), (35, 0.02), (36, 0.02), (37, 0.02), (38, 0.02), (39, 0.02), (40, 0.02), (41, 0.02), (42, 0.02), (43, 0.02), (44, 0.02), (45, 0.02), (46, 0.02), (47, 0.02), (48, 0.02), (49, 0.02)]
[(6, 0.34202757), (43, 0.6099498)]
[(29, 0.8910557)]
[(15, 0.9591477)]
[(35, 0.96498334)]
[(34, 0.95543325)]
[(43, 0.92457765)]
[(12, 0.9649833)]
[(10, 0.9693608)]
[(45, 0.96078116)]
[(7, 0.9607818)]
[(22, 0.92996687)]
[(38, 0.9607811)]
[(11, 0.90195334)]
[(29, 0.95097667)]
[(5, 0.9727647)]
[(12, 0.96078104)]
[(3, 0.9

...

[(5, 0.92457885)]
[(1, 0.95097554)]
[(10, 0.75489295)]
[(0, 0.96228975)]
[(10, 0.94839776)]
[(17, 0.95737094)]
[(15, 0.9649829)]
[(31, 0.9423262)]
[(38, 0.92996705)]
[(37, 0.9554346)]
[(9, 0.92996824)]
[(20, 0.957371)]
[(28, 0.9019523)]
[(0, 0.02), (1, 0.02), (2, 0.02), (3, 0.02), (4, 0.02), (5, 0.02), (6, 0.02), (7, 0.02), (8, 0.02), (9, 0.02), (10, 0.02), (11, 0.02), (12, 0.02), (13, 0.02), (14, 0.02), (15, 0.02), (16, 0.02), (17, 0.02), (18, 0.02), (19, 0.02), (20, 0.02), (21, 0.02), (22, 0.02), (23, 0.02), (24, 0.02), (25, 0.02), (26, 0.02), (27, 0.02), (28, 0.02), (29, 0.02), (30, 0.02), (31, 0.02), (32, 0.02), (33, 0.02), (34, 0.02), (35, 0.02), (36, 0.02), (37, 0.02), (38, 0.02), (39, 0.02), (40, 0.02), (41, 0.02), (42, 0.02), (43, 0.02), (44, 0.02), (45, 0.02), (46, 0.02), (47, 0.02), (48, 0.02), (49, 0.02)]
[(14, 0.96368635)]
[(42, 0.9591483)]
[(20, 0.85993546)]
[(43, 0.9591469)]
[(16, 0.9533109)]
[(0, 0.02), (1, 0.02), (2, 0.02), (3, 0.02), (4, 0.02), (5, 0.02), (6, 0.02), (7

[(15, 0.950977)]
[(49, 0.9673177)]
[(33, 0.89105546)]
[(2, 0.92996436)]
[(2, 0.95097625)]
[(3, 0.9573713)]
[(14, 0.7548776)]
[(11, 0.91086805)]
[(0, 0.02), (1, 0.02), (2, 0.02), (3, 0.02), (4, 0.02), (5, 0.02), (6, 0.02), (7, 0.02), (8, 0.02), (9, 0.02), (10, 0.02), (11, 0.02), (12, 0.02), (13, 0.02), (14, 0.02), (15, 0.02), (16, 0.02), (17, 0.02), (18, 0.02), (19, 0.02), (20, 0.02), (21, 0.02), (22, 0.02), (23, 0.02), (24, 0.02), (25, 0.02), (26, 0.02), (27, 0.02), (28, 0.02), (29, 0.02), (30, 0.02), (31, 0.02), (32, 0.02), (33, 0.02), (34, 0.02), (35, 0.02), (36, 0.02), (37, 0.02), (38, 0.02), (39, 0.02), (40, 0.02), (41, 0.02), (42, 0.02), (43, 0.02), (44, 0.02), (45, 0.02), (46, 0.02), (47, 0.02), (48, 0.02), (49, 0.02)]
[(14, 0.8599334)]
[(0, 0.02), (1, 0.02), (2, 0.02), (3, 0.02), (4, 0.02), (5, 0.02), (6, 0.02), (7, 0.02), (8, 0.02), (9, 0.02), (10, 0.02), (11, 0.02), (12, 0.02), (13, 0.02), (14, 0.02), (15, 0.02), (16, 0.02), (17, 0.02), (18, 0.02), (19, 0.02), (20, 0.02), (21,

[(7, 0.89106107)]
[(0, 0.02), (1, 0.02), (2, 0.02), (3, 0.02), (4, 0.02), (5, 0.02), (6, 0.02), (7, 0.02), (8, 0.02), (9, 0.02), (10, 0.02), (11, 0.02), (12, 0.02), (13, 0.02), (14, 0.02), (15, 0.02), (16, 0.02), (17, 0.02), (18, 0.02), (19, 0.02), (20, 0.02), (21, 0.02), (22, 0.02), (23, 0.02), (24, 0.02), (25, 0.02), (26, 0.02), (27, 0.02), (28, 0.02), (29, 0.02), (30, 0.02), (31, 0.02), (32, 0.02), (33, 0.02), (34, 0.02), (35, 0.02), (36, 0.02), (37, 0.02), (38, 0.02), (39, 0.02), (40, 0.02), (41, 0.02), (42, 0.02), (43, 0.02), (44, 0.02), (45, 0.02), (46, 0.02), (47, 0.02), (48, 0.02), (49, 0.02)]
[(5, 0.9423259)]
[(17, 0.9182888)]
[(42, 0.97350085)]
[(49, 0.96078074)]
[(34, 0.9509758)]
[(27, 0.94839764)]
[(33, 0.54206216), (46, 0.41617882)]
[(30, 0.9455305)]
[(32, 0.9346362)]
[(32, 0.9346353)]
[(30, 0.9299674)]
[(7, 0.9483952)]
[(31, 0.94232565)]
[(39, 0.92996675)]
[(0, 0.02), (1, 0.02), (2, 0.02), (3, 0.02), (4, 0.02), (5, 0.02), (6, 0.02), (7, 0.02), (8, 0.02), (9, 0.02), (10, 0

[(30, 0.9702888)]
[(8, 0.9182954)]
[(15, 0.9387206)]
[(30, 0.91086775)]
[(34, 0.9182967)]
[(30, 0.89105994)]
[(26, 0.9245781)]
[(46, 0.9683718)]
[(30, 0.90195495)]
[(35, 0.9622903)]
[(14, 0.9607808)]
[(47, 0.9019527)]
[(0, 0.02), (1, 0.02), (2, 0.02), (3, 0.02), (4, 0.02), (5, 0.02), (6, 0.02), (7, 0.02), (8, 0.02), (9, 0.02), (10, 0.02), (11, 0.02), (12, 0.02), (13, 0.02), (14, 0.02), (15, 0.02), (16, 0.02), (17, 0.02), (18, 0.02), (19, 0.02), (20, 0.02), (21, 0.02), (22, 0.02), (23, 0.02), (24, 0.02), (25, 0.02), (26, 0.02), (27, 0.02), (28, 0.02), (29, 0.02), (30, 0.02), (31, 0.02), (32, 0.02), (33, 0.02), (34, 0.02), (35, 0.02), (36, 0.02), (37, 0.02), (38, 0.02), (39, 0.02), (40, 0.02), (41, 0.02), (42, 0.02), (43, 0.02), (44, 0.02), (45, 0.02), (46, 0.02), (47, 0.02), (48, 0.02), (49, 0.02)]
[(7, 0.8599323)]
[(19, 0.8039116)]
[(47, 0.95097613)]
[(4, 0.9299668)]
[(1, 0.9573711)]
[(0, 0.02), (1, 0.02), (2, 0.02), (3, 0.02), (4, 0.02), (5, 0.02), (6, 0.02), (7, 0.02), (8, 0.02), (9,

[(4, 0.9591475)]
[(47, 0.92457986)]
[(0, 0.9683712)]
[(26, 0.9607813)]
[(3, 0.9483968)]
[(31, 0.94553024)]
[(0, 0.02), (1, 0.02), (2, 0.02), (3, 0.02), (4, 0.02), (5, 0.02), (6, 0.02), (7, 0.02), (8, 0.02), (9, 0.02), (10, 0.02), (11, 0.02), (12, 0.02), (13, 0.02), (14, 0.02), (15, 0.02), (16, 0.02), (17, 0.02), (18, 0.02), (19, 0.02), (20, 0.02), (21, 0.02), (22, 0.02), (23, 0.02), (24, 0.02), (25, 0.02), (26, 0.02), (27, 0.02), (28, 0.02), (29, 0.02), (30, 0.02), (31, 0.02), (32, 0.02), (33, 0.02), (34, 0.02), (35, 0.02), (36, 0.02), (37, 0.02), (38, 0.02), (39, 0.02), (40, 0.02), (41, 0.02), (42, 0.02), (43, 0.02), (44, 0.02), (45, 0.02), (46, 0.02), (47, 0.02), (48, 0.02), (49, 0.02)]
[(39, 0.92458)]
[(19, 0.9591468)]
[(20, 0.9824916)]
[(20, 0.9824916)]
[(46, 0.9509768)]
[(0, 0.02), (1, 0.02), (2, 0.02), (3, 0.02), (4, 0.02), (5, 0.02), (6, 0.02), (7, 0.02), (8, 0.02), (9, 0.02), (10, 0.02), (11, 0.02), (12, 0.02), (13, 0.02), (14, 0.02), (15, 0.02), (16, 0.02), (17, 0.02), (18, 0.

In [26]:
# extract the scores and round them to 3 decimal places
#scores = np.round([[doc[1] for doc in row] for row in lda_docs], 3)
scores = [[doc[1] for doc in row] for row in lda_docs]
scores

[[0.9108701],
 [0.80390525],
 [0.95914805],
 [0.9591478],
 [0.8599378],
 [0.9573714],
 [0.8910629],
 [0.83659464],
 [0.8599399],
 [0.95737094],
 [0.9636869],
 [0.929968],
 [0.9346354],
 [0.9423245],
 [0.96368647],
 [0.96368575],
 [0.95736986],
 [0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02],
 [0.9019529],
 [0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.02,
  0.0

In [27]:
# convert the documents scores into a data frame
df_lda = pd.DataFrame(scores, columns=["topic 1", "topic 2", "topic 3", "topic 4", "topic 5", "topic 6", "topic 7", "topic 8", "topic 9", "topic 10", "topic 11", "topic 12", "topic 13", "topic 14", "topic 15", "topic 16", "topic 17", "topic 18", "topic 19", "topic 20", "topic 21", "topic 22", "topic 23", "topic 24", "topic 25", "topic 26", "topic 27", "topic 28", "topic 29", "topic 30", "topic 31", "topic 32", "topic 33", "topic 34", "topic 35", "topic 36", "topic 37", "topic 38", "topic 39", "topic 40", "topic 41", "topic 42", "topic 43", "topic 44", "topic 45", "topic 46", "topic 47", "topic 48", "topic 49", "topic 50"])
df_lda

topic 1  topic 2  topic 3  topic 4  topic 5  topic 6  topic 7  topic 8  \
0     0.910870      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
1     0.803905      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
2     0.959148      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
3     0.959148      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
4     0.859938      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
...        ...      ...      ...      ...      ...      ...      ...      ...   
9953  0.901955      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
9954  0.924579      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
9955  0.942328      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
9956  0.957369      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
9957  0.934637      NaN      NaN      NaN      NaN      NaN      NaN      NaN   

      topic 9  topic 10  ...  topic 41  topic 42  topic 43  topic 44  \
0         NaN       NaN  ...       NaN       NaN       NaN       NaN   
1         NaN       NaN  ...       NaN       NaN       NaN       NaN   
2         NaN       NaN  ...       NaN       NaN       NaN       NaN   
3         NaN       NaN  ...       NaN       NaN       NaN       NaN   
4         NaN       NaN  ...       NaN       NaN       NaN       NaN   
...       ...       ...  ...       ...       ...       ...       ...   
9953      NaN       NaN  ...       NaN       NaN       NaN       NaN   
9954      NaN       NaN  ...       NaN       NaN       NaN       NaN   
9955      NaN       NaN  ...       NaN       NaN       NaN       NaN   
9956      NaN       NaN  ...       NaN       NaN       NaN       NaN   
9957      NaN       NaN  ...       NaN       NaN       NaN       NaN   

      topic 45  topic 46  topic 47  topic 48  topic 49  topic 50  
0          NaN       NaN       NaN       NaN       NaN       NaN  
1          NaN       NaN       NaN       NaN       NaN       NaN  
2          NaN       NaN       NaN       NaN       NaN       NaN  
3          NaN       NaN       NaN       NaN       NaN       NaN  
4          NaN       NaN       NaN       NaN       NaN       NaN  
...        ...       ...       ...       ...       ...       ...  
9953       NaN       NaN       NaN       NaN       NaN       NaN  
9954       NaN       NaN       NaN       NaN       NaN       NaN  
9955       NaN       NaN       NaN       NaN       NaN       NaN  
9956       NaN       NaN       NaN       NaN       NaN       NaN  
9957       NaN       NaN       NaN       NaN       NaN       NaN  

[9958 rows x 50 columns]

In [28]:
df_lda=df_lda.fillna(0)
df_lda

topic 1  topic 2  topic 3  topic 4  topic 5  topic 6  topic 7  topic 8  \
0     0.910870      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
1     0.803905      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
2     0.959148      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
3     0.959148      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4     0.859938      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
...        ...      ...      ...      ...      ...      ...      ...      ...   
9953  0.901955      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
9954  0.924579      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
9955  0.942328      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
9956  0.957369      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
9957  0.934637      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

      topic 9  topic 10  ...  topic 41  topic 42  topic 43  topic 44  \
0         0.0       0.0  ...       0.0       0.0       0.0       0.0   
1         0.0       0.0  ...       0.0       0.0       0.0       0.0   
2         0.0       0.0  ...       0.0       0.0       0.0       0.0   
3         0.0       0.0  ...       0.0       0.0       0.0       0.0   
4         0.0       0.0  ...       0.0       0.0       0.0       0.0   
...       ...       ...  ...       ...       ...       ...       ...   
9953      0.0       0.0  ...       0.0       0.0       0.0       0.0   
9954      0.0       0.0  ...       0.0       0.0       0.0       0.0   
9955      0.0       0.0  ...       0.0       0.0       0.0       0.0   
9956      0.0       0.0  ...       0.0       0.0       0.0       0.0   
9957      0.0       0.0  ...       0.0       0.0       0.0       0.0   

      topic 45  topic 46  topic 47  topic 48  topic 49  topic 50  
0          0.0       0.0       0.0       0.0       0.0       0.0  
1          0.0       0.0       0.0       0.0       0.0       0.0  
2          0.0       0.0       0.0       0.0       0.0       0.0  
3          0.0       0.0       0.0       0.0       0.0       0.0  
4          0.0       0.0       0.0       0.0       0.0       0.0  
...        ...       ...       ...       ...       ...       ...  
9953       0.0       0.0       0.0       0.0       0.0       0.0  
9954       0.0       0.0       0.0       0.0       0.0       0.0  
9955       0.0       0.0       0.0       0.0       0.0       0.0  
9956       0.0       0.0       0.0       0.0       0.0       0.0  
9957       0.0       0.0       0.0       0.0       0.0       0.0  

[9958 rows x 50 columns]

In [29]:
from __future__ import print_function
import time
import numpy as np
import pandas as pd
#from sklearn.datasets import fetch_mldata
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE
%matplotlib inline
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
import seaborn as sns

In [30]:
N = 9958
rndperm = np.random.permutation(df_lda.shape[0])
df_subset = df_lda.loc[rndperm[:N],:].copy()
#data_subset = df_subset[feat_cols].values
data_subset = df_subset.values
pca = PCA(n_components=3)
pca_result = pca.fit_transform(data_subset)
df_subset['pca-one'] = pca_result[:,0]
df_subset['pca-two'] = pca_result[:,1] 
df_subset['pca-three'] = pca_result[:,2]
print('Explained variation per principal component: {}'.format(pca.explained_variance_ratio_))

Explained variation per principal component: [9.17020351e-01 8.16123004e-02 7.26937723e-04]


In [31]:
df_subset

topic 1  topic 2  topic 3  topic 4  topic 5  topic 6  topic 7  topic 8  \
8616  0.901955      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
5074  0.942327      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
5421  0.968371      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
6482  0.963685      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
8768  0.963686      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
...        ...      ...      ...      ...      ...      ...      ...      ...   
5392  0.877445      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
3177  0.950978      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
5517  0.754880      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4541  0.945530      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
1692  0.948396      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

      topic 9  topic 10  ...  topic 44  topic 45  topic 46  topic 47  \
8616      0.0       0.0  ...       0.0       0.0       0.0       0.0   
5074      0.0       0.0  ...       0.0       0.0       0.0       0.0   
5421      0.0       0.0  ...       0.0       0.0       0.0       0.0   
6482      0.0       0.0  ...       0.0       0.0       0.0       0.0   
8768      0.0       0.0  ...       0.0       0.0       0.0       0.0   
...       ...       ...  ...       ...       ...       ...       ...   
5392      0.0       0.0  ...       0.0       0.0       0.0       0.0   
3177      0.0       0.0  ...       0.0       0.0       0.0       0.0   
5517      0.0       0.0  ...       0.0       0.0       0.0       0.0   
4541      0.0       0.0  ...       0.0       0.0       0.0       0.0   
1692      0.0       0.0  ...       0.0       0.0       0.0       0.0   

      topic 48  topic 49  topic 50   pca-one   pca-two  pca-three  
8616       0.0       0.0       0.0 -0.056700 -0.008237  -0.000176  
5074       0.0       0.0       0.0 -0.096463 -0.004572   0.000042  
5421       0.0       0.0       0.0 -0.122114 -0.002207   0.000182  
6482       0.0       0.0       0.0 -0.117499 -0.002632   0.000157  
8768       0.0       0.0       0.0 -0.117500 -0.002632   0.000157  
...        ...       ...       ...       ...       ...        ...  
5392       0.0       0.0       0.0 -0.032560 -0.010462  -0.000309  
3177       0.0       0.0       0.0 -0.104984 -0.003786   0.000088  
5517       0.0       0.0       0.0  0.088155 -0.021591  -0.000970  
4541       0.0       0.0       0.0 -0.099618 -0.004281   0.000059  
1692       0.0       0.0       0.0 -0.102440 -0.004020   0.000074  

[9958 rows x 53 columns]

In [32]:
from sklearn.manifold import TSNE
tsne_model = TSNE(n_components=2, verbose=1, random_state=7, angle=.99, init='pca')
# 13-D -> 2-D
tsne_lda = tsne_model.fit_transform(df_subset) # doc_topic is document-topic matrix from LDA or GuidedLDA 

[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 9958 samples in 0.001s...
[t-SNE] Computed neighbors for 9958 samples in 5.218s...
[t-SNE] Computed conditional probabilities for sample 1000 / 9958
[t-SNE] Computed conditional probabilities for sample 2000 / 9958
[t-SNE] Computed conditional probabilities for sample 3000 / 9958
[t-SNE] Computed conditional probabilities for sample 4000 / 9958
[t-SNE] Computed conditional probabilities for sample 5000 / 9958
[t-SNE] Computed conditional probabilities for sample 6000 / 9958
[t-SNE] Computed conditional probabilities for sample 7000 / 9958
[t-SNE] Computed conditional probabilities for sample 8000 / 9958
[t-SNE] Computed conditional probabilities for sample 9000 / 9958
[t-SNE] Computed conditional probabilities for sample 9958 / 9958
[t-SNE] Mean sigma: 0.000000
[t-SNE] KL divergence after 250 iterations with early exaggeration: 56.722054
[t-SNE] KL divergence after 1000 iterations: 0.242050


In [33]:
from sklearn.manifold import TSNE
from bokeh.plotting import figure, output_file, show
from bokeh.models import Label
from bokeh.io import output_notebook

import matplotlib.colors as mcolors

# Plot the Topic Clusters using Bokeh
output_notebook()
n_topics = 50
mycolors = np.array([color for name, color in mcolors.TABLEAU_COLORS.items()])
plot = figure(title="t-SNE Clustering of {} LDA Topics".format(n_topics), 
              plot_width=400, plot_height=400)
#plot.scatter(x=tsne_lda[:,0], y=tsne_lda[:,1], color=mycolors[topic_num])
plot.scatter(x=tsne_lda[:,0], y=tsne_lda[:,1], color=mycolors)
show(plot)

Loading BokehJS ...